# Show the data

In [1]:
import pandas as pd
from iron_handmaidens.data.src.emg import EMGData
import plotly.graph_objects as go
import plotly.express as px

In [2]:
left = EMGData.read_csv('test_data/participant1/A/Shimmer_4680.csv')
right = EMGData.read_csv('test_data/participant1/A/Shimmer_5470.csv')
center = left + right

In [5]:
left.df[left[['CH']]] = left.normalize(left[['CH']])
left.df

Timestamp_4680  Status_4680  CH1_4680  CH2_4680  Event_4680
0          1.635975e+12        128.0  0.725007  0.624337         0.0
1          1.635975e+12        128.0  0.741815  0.622718        -1.0
2          1.635975e+12        128.0  0.754829  0.620824        -1.0
3          1.635975e+12        128.0  0.757222  0.622787        -1.0
4          1.635975e+12        128.0  0.763292  0.628367        -1.0
...                 ...          ...       ...       ...         ...
1540876    1.635976e+12        128.0  1.683105  0.160708        -1.0
1540877    1.635976e+12        128.0  1.683805  0.159985        -1.0
1540878    1.635976e+12        128.0  1.685089  0.159916        -1.0
1540879    1.635976e+12        128.0  1.683572  0.160329        -1.0
1540880    1.635976e+12        128.0  1.685556  0.160398        -1.0

[1540881 rows x 5 columns]

In [3]:
left.preprocess()
left.figure().show()

In [4]:
left.quartiles()

CH1_4680  CH2_4680
0.9  2.127708  2.714297
0.5  0.796343  0.593681
0.1  0.068035 -0.775668

In [5]:
right.preprocess()
right.figure().show()

In [6]:
# center.preprocess()
center.maxDataPoints = 10000
center.figure().show()

In [7]:
center.quartiles()

CH1_4680  CH2_4680  CH1_5470  CH2_5470
0.9  2.128309  2.714057  0.708234  4.752214
0.5  0.796343  0.593441 -0.395587 -0.512304
0.1  0.067915 -0.776029 -1.133812 -1.908459

In [8]:
import numpy as np
import plotly.express as px
import plotly.graph_objects as go
df = px.data.gapminder().query("year == 2007")

fig = go.Figure()
# adding names for reference
fig.add_scatter(mode="markers", x=df["gdpPercap"], y=df["lifeExp"], 
                visible = False, name='linear')
fig.add_scatter(mode="markers", x=df["gdpPercap"], y=np.sqrt(df["lifeExp"]), 
                visible = False, name='sqrt')

# buttons for updatemenu
buttons = [dict(method='restyle',
                label='linear',
                visible=True,
                args=[{'label': 'linear',
                       'visible':[True, False],}]),
           dict(method='restyle',
                label='sqrt',
                visible=True,
                args=[{'label': 'linear',
                       'visible':[False, True],}])]
           
# specify updatemenu        
um = [{'buttons':buttons, 'direction': 'down'}]
fig.update_layout(updatemenus=um)

# Conditionally Updating Traces 
fig.for_each_trace(
    lambda trace: trace.update(visible=True) if trace.name == "linear" else (),
)
fig.add_vline(10000, name='Jeff')
fig.show()

In [9]:
left.df['Toggle'] = left.df[left['Event']].diff()
toggles = left.df.loc[abs(left.df['Toggle']) == 3]
toggles = toggles.reset_index()
toggles

index  Timestamp_4680  Status_4680  CH1_4680  CH2_4680  Event_4680  \
0    39268    1.635975e+12        128.0  3.375533  2.649508         2.0   
1    45657    1.635975e+12        128.0  1.595330  3.059159        -1.0   
2    86663    1.635975e+12        128.0  2.819595  2.237934         2.0   
3    94785    1.635975e+12        128.0  1.107668  2.366791        -1.0   
4   469831    1.635975e+12        128.0  0.627458  2.181920         2.0   
5  1415977    1.635976e+12        128.0  0.560866 -0.834207        -1.0   
6  1449111    1.635976e+12        128.0  0.065390 -0.541393         2.0   
7  1456384    1.635976e+12        128.0  0.913420 -0.567717        -1.0   
8  1512873    1.635976e+12        128.0  2.873446 -1.288693         2.0   
9  1520821    1.635976e+12        128.0  2.453578 -0.041590        -1.0   

    Elapse (s)  Moving Average 1_4680  Moving Average 2_4680  Toggle  
0    38.347656               2.997006               2.493343     3.0  
1    44.586914               1.816207               3.290592    -3.0  
2    84.631836               2.740863               2.236253     3.0  
3    92.563477               0.827724               2.279461    -3.0  
4   458.819336               0.542847               2.038300     3.0  
5  1382.790039               0.596585              -0.755628    -3.0  
6  1415.147461              -0.074934              -0.581324     3.0  
7  1422.250000               0.962916              -0.644719    -3.0  
8  1477.415039               2.902340              -1.153909     3.0  
9  1485.176758               2.545596              -0.154790    -3.0

In [10]:
fig = go.Figure()
plots = []
for line in left.find_columns('CH'):
	newFig = go.Scatter(x=left.df.iloc[::100][left['Elapse']], y=left.df[line].iloc[::100], name=line, visible='legendonly')
	plots.append(newFig)
[fig.add_trace(plot) for plot in plots]
fig.for_each_trace(lambda trace: trace.update(visible=True) if trace.name == 'CH1_4680' else ())

for i in range(0, len(toggles)-1, 2):
	fig.add_vrect(toggles.iloc[i][left['Elapse']], toggles.iloc[i+1][left['Elapse']], fillcolor='green', opacity=0.25)

fig.show()

In [11]:
def find_events(emgData):
	new = pd.DataFrame()

	emgData.df['Toggle'] = emgData.df[emgData['Event']].diff()
	new = emgData.df.loc[abs(emgData.df['Toggle']) == 3]
	new = new.reset_index()
	
	return new

In [14]:
left.df[left['Timestamp']].astype(int).duplicated().value_counts()

False    1504729
True       36152
Name: Timestamp_4680, dtype: int64